# TP 3 : Chiffrement asymétrique El Gamal
## Chiffrement d’El Gamal
Le chiffrement d’El Gamal est un protocole de cryptographie asymétrique inventé par Taher El Gamal
en 1984 et qui repose sur le problème du logarithme discret.
## Génération des clefs.
La première étape du schéma de chiffrement consiste à produire une paire de clefs : la clef publique,
et la clef secrète (ou clé privée). La première servira à chiffrer les messages et la deuxième à les
déchiffrer.
Pour générer sa paire de clefs, il faut d’abord choisir un nombre premier p et un générateur g pour
Z/pZ.
Ensuite il faut choisir un élément s de Z/pZ qui constituera la clef privée, et calculer h = g
s mod p.
Pour terminer, la clé publique est (p, g, h).
## Chiffrement
Pour chiffrer un message M encodé comme un entier de Z/pZ avec la clé publique (p, g, h), il faut
tirer au hasard un aléa r dans Z/pZ et calculer C1 = g
r mod p et C2 = (M ·(h
r mod p)) mod p.
Ainsi le chiffré C est composé de ces deux nombres : C = (C1, C2).
## Déchiffrement
Ayant accès à C = (C1, C2) et à la clé privée s, pour déchiffrer il suffit de calculer :

C2 × ((C1)
s mod p)
−1 mod p

mod p
pour retrouver le message M

In [54]:
from sympy import randprime
from sympy import mod_inverse
from random import randint

# Exercice 1

## (Génération des clefs). 
Écrivez une fonction Python3 Clefs(k) qui permet de générer
une paire de clefs El Gamal, avec un module compris entre 2k et 2k+1 − 1.
La taille compte ! Plus vos clés seront de grands nombres, plus elles seront sûres. Le « paramètre de
sécurité » est donc le nombre de bits du module p, autrement dit son logarithme binaire k.
Vous aurez peut-être l’usage de la fonction randprime de la bibliothèque sympy (éventuellement à
installer en tapant pip install sympy dans un terminal) et de la fonction randint de la bibliothèque random. Pour calculer x
n mod p vous devrez utiliser pow(x, n, mod=p) car (x**n)%p ne
marche pas pour les grands nombres. Attention, ce n’est pas une fonction de la bibliothèque math ! !
### 1. Choisissez comme module un nombre premier p au hasard compris entre 2k et 2k+1 − 1.
### 2. Choisissez comme générateur un nombre g au hasard compris entre 2 et p − 1.
Remarque : Votre « générateur » n’en est peut-être pas un. Pour gagner du temps, on ne
vous demande pas de le vérifier : la procédure de chiffrement/déchiffrement marche encore,
mais votre clé sera plus facile à casser, car il y aura plusieurs valeurs possibles pour s, en plus
de celle qui sera vraiment votre clé secrète.
### 3. Choisissez comme secret un nombre s au hasard compris entre 2 et p − 1.
### 4. Calculez h.

In [33]:
def Clef(k):
    p = randprime(2**k, 2**(k+1) - 1)
    g = randint(2, p)
    s = randint(2, p)
    h = pow(g, s, mod=p)
    return (p, g, h), s

In [34]:
print(Clef(5))

((59, 59, 0), 2)


# Exercice 2. 
## Écrivez une fonction Python3 Chiffrer(...) qui permet de chiffrer un nombre M avec le chiffrement d’El Gamal.

In [35]:
def Chiffrer(M, p, g, h):
    r = randint(0, p)
    C1 = pow(g, r, mod=p)
    C2 = (M * pow(h, r, mod=p))%p
    return C1, C2

In [57]:
print("Génération de clef : ")
public, prive = Clef(10)
print("Clef public : ", public)
print("Clef privé : ",  prive)
M = 1200
C = Chiffrer(M, public[0], public[1], public[2])
print("Chiffrement de ", M, "Soit un chiffré c = ", C)

Génération de clef : 
Clef public :  (1871, 1240, 1473)
Clef privé :  1063
Chiffrement de  1200 Soit un chiffré c =  (973, 292)


# Exercice 3. 
## Écrivez une fonction Python3 Dechiffrer(...) qui permet de déchiffrer un chiffré (C1, C2) avec le chiffrement d’El Gamal.
Vous pouvez calculer l’inverse de x modulo p (s’il existe) par pow(x, -1, p).

In [58]:
def Dechiffrer(C1, C2, s, p):
    M = (C2 * mod_inverse(pow(C1, s, mod=p), p))%p
    return M

In [59]:
print("Message à déchiffrer : ", C)
Md = Dechiffrer(C[0], C[1], prive, public[0])
print("Resultat après déchiffrement : ", Md)

Message à déchiffrer :  (973, 292)
Resultat après déchiffrement :  1200


# Exercice 4. 
Fondamentalement, le chiffrement d’El Gamal s’applique à des nombres. Mais très souvent, les messages qu’on souhaite chiffrer sont plutôt des textes ! Pour chiffrer des textes, il faut donc passer par une étape préalable de numérisation des caractères qui le composent.
### 1. Écrivez une fonction Python3 Encode(texte) qui convertit une chaîne de caractères texte en un nombre entier. Il y a plusieurs manières de faire cela, voici celle que nous proposons ici :
(a) Chaque caractère est encodé par son code ASCII décimal, composé de 1, 2 ou 3 chiffres. Étant donné un caractère c, le code ASCII correspondant est obtenu par ord(c).  
(b) Les codes ASCII des caractères sont transformés en str, puis ramenés sur 3 chiffres en ajoutant si nécessaire des 0 à gauche.   
(c) Les chaînes représentant les codes ASCII sur 3 chiffres sont concaténées les unes à la suite des autres pour obtenir une seule (grande) chaîne, ensuite transformée en int.  
### 2. Écrivez une fonction Python3 Decode(nombre) effectuant l’opération réciproque : étant donné un nombre entier nombre, retrouver la chaîne de caractères texte qu’il représente.
Pour cela, utilisez la fonction chr. Étant un code ASCII donné num, le caractère associé est
obtenu par chr(num).
Pour récupérer les codes ASCII des différents caractères, vous voudrez peut-être utiliser le
reste (%) et le quotient (//) de la division par 1000.
### 3. Testez vos fonctions d’encodage/décodage. On doit avoir, pour tout message M :
M=Decode(Encode(M))

In [171]:
def Encode(texte):
    newTexte = ""
    for i in range(len(texte)):
        newTexte = newTexte + str(ord(texte[i])).zfill(3)
    intTexte = int(newTexte)
    return intTexte

In [168]:
Encode("Essai")

69115115097105

In [184]:
def Decode(nb):
    res = ""
    while nb > 0 :
        res = chr(nb % 1000) + res
        nb = nb // 1000
    return res

In [185]:
Decode(69115115097105)

'Essai'

In [179]:
Chiffrer(Encode("Yoloyolo boys"), 2300342751692871968900072455807, 1945803074531676481815246424499, 150618869292435473863944805702)

(1443295143187065358570471830895, 895427499536852088675129942696)

# Exercice 7 
(Exponentielle).
### 1. Écrire une fonction exp_basique(x,n,p) qui, pour trois entiers positifs x, n, p donnés en entrée, calcule de manière basique (sans utiliser la bibliothèque math) l’exponentielle modulaire x n mod p
### 2. L’algorithme d’exponentielle rapide permet également de calculer le nombre x n mod p mais en utilisant l’algorithme récursif suivant :
puissance(x, n) =



x, si n = 1
puissance(x
2
, n/2), si n est pair
x × puissance(x
2
, (n − 1)/2), si n est impair  
Écrire une fonction exp_rapide(x,n,p) implémentant cet algorithme.
### 3. Calculer le nombre suivant, avec les deux méthodes :
123456789123456789 (mod 987654321) = 598987215
Que constatez-vous ?

In [188]:
def exp_basique(x, n, p):
    return (x**n)%p

In [192]:
print(exp_basique(973, 2, 1871))
print(pow(973, 2, 1871))

3
3


In [ ]:
def exp_rapide(x, n, p):
    if(n = 1):
        return x
    if(n%2 = 0):
        return puissance(x, n, p)